In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import copy


In [2]:
data = pd.read_csv("../data/txn_by_dept.csv")
data.head()

POS Txn                       Dept   ID  Sales U
0  16120100160021008773               0261:HOSIERY  250        2
1  16120100160021008773  0634:VITAMINS & HLTH AIDS  102        1
2  16120100160021008773          0879:PET SUPPLIES  158        2
3  16120100160021008773                 0973:CANDY  175        2
4  16120100160021008773               0982:SPIRITS  176        1

In [3]:
depts = set(data['Dept'])
transactions = set(data['POS Txn'])
data["ID"] = data["ID"].astype(str)
ids = set(data["ID"])

In [4]:
print(ids)

{'213', '72', '156', '8', '133', '108', '93', '76', '24', '132', '266', '35', '99', '61', '113', '19', '184', '171', '60', '104', '273', '158', '263', '63', '128', '146', '59', '149', '177', '12', '268', '135', '160', '277', '28', '9', '235', '32', '148', '42', '157', '7', '75', '306', '13', '41', '131', '23', '81', '27', '141', '272', '178', '134', '170', '219', '110', '48', '154', '50', '14', '55', '138', '105', '77', '18', '97', '5', '30', '242', '17', '297', '65', '3', '71', '46', '169', '1', '265', '52', '100', '36', '264', '78', '129', '70', '106', '82', '296', '183', '6', '270', '292', '107', '58', '147', '38', '56', '51', '80', '167', '295', '29', '310', '57', '294', '49', '54', '45', '155', '73', '179', '34', '37', '176', '269', '202', '185', '182', '150', '2', '10', '122', '288', '111', '309', '74', '307', '31', '40', '200', '308', '64', '85', '79', '278', '86', '165', '144', '109', '175', '94', '164', '305', '53', '204', '152', '102', '250', '44', '311', '11', '87', '166', '

In [5]:
adj_matrix = pd.DataFrame(columns = ids, index = transactions, data = np.zeros((len(transactions), len(ids))))
for row in data.iterrows():
    adj_matrix[row[1][2]].loc[row[1][0]] += 1


# mask = adj_matrix>=1
# adj_matrix_binary = adj_matrix.mask(adj_matrix >= 1, 1)
adj_matrix.head()   

213   72  156    8  133  108   93   76   24  132  ...  \
16120100160034005060  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005061  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005062  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005063  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
16120100160034005064  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   

                      311   11   87  166   22  151   26   21  143  214  
16120100160034005060  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005061  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005062  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  
16120100160034005063  0.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  
16120100160034005064  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[5 rows x 160 columns]

In [6]:
support = []
relative_support = []
for col in adj_matrix.columns: 
    support.append(adj_matrix[col].sum())
    relative_support.append(adj_matrix[col].sum()/len(adj_matrix))


In [7]:
def get_candidates(k, frequents):
    j = k-1
    candidates = []    
    if k > 1:
#             print('here ', k)
            for f1 in range(len(frequents)):
                for f2 in range(f1+1, len(frequents)):
                    if frequents[f1][0:j]==frequents[f2][0:j]:
#                         print('f1', frequents[f1][0:j+1])
#                         print('f2', frequents[f2][j:])
                        candidates.append(frequents[f1][0:j+1]+frequents[f2][j:])
#             print('candidates:', ca    # just work w    # just work way through by removing one each timeay through by removing one each timendidates)
    else:
        for f1 in range(len(frequents)):
            for f2 in range(f1+1, len(frequents)):
                candidates.append([frequents[f1],frequents[f2]])
    
    return candidates

In [8]:
def frequent_item_sets(adj_matrix, C1_itemset, min_sup):
    support_dict = {}
    binary_matrix = adj_matrix.copy()
    max_itemset = len(C1_itemset)
    candidates = C1_itemset
    
    frequents = []
    supports = []
    for candidate in candidates:
        support = binary_matrix[candidate].sum()
        

        if support >= min_sup:
                frequents.append(candidate)
                supports.append(support)
#                 print(candidate, support)

    if len(frequents) == 0:
        return support_dict

    support_dict[1] = [frequents, supports]
    candidates = get_candidates(1, frequents)
                    
    for k in range(2, max_itemset):
        print(k)
        frequents = []
        supports = []
        for candidate in candidates:
            support = binary_matrix.where(binary_matrix[candidate].sum(axis=1) == len(candidate)).sum().max()
#             support = binary_matrix[candidate].sum()
            if support >= min_sup:
                frequents.append(candidate)
                supports.append(support)
#                 print(candidate, support)

                
        if len(frequents) == 0:
            print('No Frequents')
            return support_dict
        
        support_dict[k] = [frequents, supports]
#         print(frequents)
        
        
        candidates = get_candidates(k, frequents)
#         print('full candidates ', candidates)
        candidates = prune_candidates(candidates, frequents)
#         print('pruned ', candidates)

    return support_dict

In [9]:
def prune_candidates(candidates, frequent_set):
    pruned_list = []
    
    for c in range(len(candidates)):
        prune_flag = False
        for i in range(len(candidates[c])):
#             try:
            temp = copy.deepcopy(candidates[c])
            temp.pop(i)
            if temp not in frequent_set:
                prune_flag = True
                break
        if not prune_flag:
            pruned_list.append(candidates[c])
#             except:
#                 print('candidate ', candidates[c])
#                 print('temp', temp)
#                 print('pruned_list', pruned_list)
    return pruned_list

In [10]:
def get_antecedents(parent_set, frequency_dict, max_key):
    antecedents = []
    for key in frequency_dict.keys():
        if key < max_key:
            f_set = frequency_dict[key]
            print('f_set', list(f_set[0][1]))
#             print('f_set_can', f_set[0])
#             print('f_set_sup', f_set[1])
            for i in range(len(f_set[0])):
                print(f_set[0][i])
                if len(list(f_set[0][i]))==1:
                    temp = [f_set[0][i]]
                else:
                    temp = f_set[0][i]
#                 print(set(temp))
#                 print(set(parent_set))
                if set(temp).issubset(set(parent_set)):
#                     print(temp,f_set[1][i])
                    antecedents.append([temp,f_set[1][i]])
                
        else:
            break
                                        
                    
    return antecedents
                
    

In [11]:
def get_association_rules(frequency_dict, min_conf):
    confidence_dict = []
    for key in frequency_dict.keys():
        if key > 1:
            for i in range(len(frequency_dict[key][0])):
                z = frequency_dict[key][0][i]
                z_sup = frequency_dict[key][1][i]
                print('parent set: ', z, z_sup)
                antecedents = get_antecedents(z, frequency_dict, key)
#                 print('antecedents: ', antecedents)
                
#                 for antecedent in antecedents:
                while len(antecedents) > 0:
                    antecedent = antecedents.pop()
                    x = set(antecedent[0])
                    x_sup = antecedent[1]
                    print('X', x, x_sup)
                    y = set(z)-x
#                     for compliment in antecedents:
#                         if set(compliment[0]) == y:
#                             y_sup = compliment[1]
#                             print('Y', y, y_sup)
                    confidence = z_sup/x_sup
                    print(x, '->', y, confidence)
                    if confidence >= min_conf:
                        confidence_dict.append([list(x),list(y), confidence])
                    else:
                        antecedents = prune_antecedents(x, antecedents)
#                         print('pruned', antecedents)
                            
    return confidence_dict

In [12]:
def prune_antecedents(x, antecedents):
    pruned_antecedents = []
    for antecedent in antecedents:
        if set(antecedent[0]).issubset(x):
            pass
        else:
            pruned_antecedents.append(antecedent)
            
    return pruned_antecedents

In [13]:
def get_evals(confidences_list, frequency_dict, size_dataset):
    metrics = []
    for c in confidences_list:
        print('\n', c)
        confidence = c[2]
        k = len(c[1])
        frequencies = frequency_dict[k]
#         print('frequencies 0', frequencies[0])
#         print('c1', set(c[1]))
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
#             print('temp', temp)
            if set(c[1])==temp:
                support = frequencies[1][i]
        lift = confidence/(support/size_dataset)
        print('lift', lift)
        
        c.append(lift)
        
        # leverage = rel_sup(XY) - rel(x)*rel(y)
        x = set(c[0])
        y = set(c[1])
        xy = x.union(y)
#         print(x)
#         print(y)
#         print(xy)
        k = len(xy)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if xy==temp:
                support_xy = frequencies[1][i]
        rel_xy = support_xy/size_dataset
        
        x = set(c[0])
        k = len(x)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if x==temp:
                support_x = frequencies[1][i]
        rel_x = support_x/size_dataset
        
        y = set(c[1])
        k = len(y)
        frequencies = frequency_dict[k]
        for i in range(len(frequencies[0])):
            if k==1:
                temp = set([frequencies[0][i]])
            else:
                temp = set(frequencies[0][i])
            if y==temp:
                support_y = frequencies[1][i]
        rel_y = support_y/size_dataset
        
        leverage = rel_xy - rel_x*rel_y
        print('leverage', leverage)
        
        c.append(leverage)
        metrics.append([lift, leverage])
        
    return confidences_list, metrics

In [14]:
# test1 = [
# [1, 0, 1, 1, 0, 0],
# [0, 1, 0, 1, 0, 0],
# [1, 1, 1, 0, 1, 0],
# [0, 1, 0, 1, 0, 1]#,
# # [1, 1, 1, 1, 1, 0]
# ]

# test2 = [
# [1, 1, 1, 0, 0],
# [1, 1, 1, 1, 1],
# [1, 0, 1, 1, 0],
# [1, 0, 1, 1, 1],
# [1, 1, 1, 1, 0]
# ]

In [15]:
# test_df = pd.DataFrame(data=test2, columns = ['A', 'B', 'C', 'D', 'E'])
# test_df.head()

In [16]:
# frequent_test = frequent_item_sets(test_df, test_df.columns, 2)
# print('\n')
# for key in frequent_test.keys():
#     print('Item Set Length: ', key, '\n', frequent_test[key][0], '\n', frequent_test[key][1])

In [17]:
# confidence_test = get_association_rules(frequent_test, 1)

In [18]:
# for c in confidence_test:
#     print(c)

In [19]:
# evals = get_lifts(confidence_test, frequent_test, len(test_df))

In [20]:
# for row in evals[0]:
#     print(row)

In [21]:
frequent_full = frequent_item_sets(adj_matrix, adj_matrix.columns, 3)

2
3
4
5
6
7
No Frequents


In [22]:
for key in frequent_full.keys():
    print('Item Set Length: ', key, '\n', frequent_full[key])

Item Set Length:  1 
 [['213', '72', '156', '8', '133', '108', '93', '76', '24', '132', '266', '35', '99', '61', '113', '19', '171', '60', '104', '273', '158', '263', '63', '128', '146', '59', '149', '177', '12', '268', '135', '160', '28', '9', '235', '32', '148', '42', '157', '75', '13', '41', '131', '23', '81', '27', '141', '272', '178', '170', '110', '48', '154', '50', '14', '55', '138', '105', '77', '97', '5', '30', '17', '297', '65', '3', '71', '46', '169', '1', '265', '52', '100', '36', '264', '78', '70', '106', '82', '296', '183', '6', '270', '292', '107', '58', '147', '38', '56', '51', '80', '167', '295', '29', '310', '57', '294', '49', '54', '45', '155', '73', '179', '34', '37', '176', '269', '202', '185', '182', '2', '10', '122', '288', '111', '309', '74', '307', '31', '40', '308', '64', '85', '79', '278', '86', '165', '144', '109', '175', '94', '164', '53', '204', '152', '102', '250', '44', '22', '26', '21', '143', '214'], [112.0, 103.0, 38.0, 16.0, 4.0, 68.0, 200.0, 17.0, 2

In [23]:
confidence_full = get_association_rules(frequent_full, 1)

parent set:  ['72', '156'] 3.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
144
109
175
94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['72', '108'] 8.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
4

94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['72', '169'] 6.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
144
109
175
94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['72', '265'] 5.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
26

82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
144
109
175
94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['156', '110'] 10.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
144
109
175
94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['156', '100'] 5.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110


155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
144
109
175
94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['93', '24'] 4.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
144
109
175
94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['93', '99'] 42.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78

46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
144
109
175
94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['93', '176'] 24.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
144
109
175
94
164
53
204
152
102
250
44
22
26
21
143
214
parent set:  ['93', '122'] 3.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
4

...

['72', '108']
['72', '93']
['72', '266']
['72', '99']
['72', '158']
['72', '263']
['72', '177']
['72', '12']
['72', '160']
['72', '42']
['72', '272']
['72', '178']
['72', '170']
['72', '110']
['72', '138']
['72', '71']
['72', '169']
['72', '265']
['72', '100']
['72', '70']
['72', '296']
['72', '270']
['72', '147']
['72', '294']
['72', '179']
['72', '176']
['72', '278']
['72', '86']
['72', '175']
['72', '102']
['72', '250']
['72', '143']
['156', '108']
['156', '93']
['156', '158']
['156', '170']
['156', '110']
['156', '100']
['156', '292']
['156', '179']
['156', '176']
['156', '86']
['156', '175']
['156', '94']
['156', '143']
['8', '9']
['108', '93']
['108', '99']
['108', '60']
['108', '158']
['108', '177']
['108', '170']
['108', '110']
['108', '100']
['108', '36']
['108', '147']
['108', '179']
['108', '176']
['108', '86']
['108', '109']
['108', '175']
['108', '143']
['93', '24']
['93', '99']
['93', '171']
['93', '158']
['93', '177']
['93', '160']
['93', '148']
['93', '42']
['93', '27']

['93', '99', '100', '143']
['93', '99', '86', '175']
['93', '99', '175', '143']
['93', '99', '26', '143']
['93', '178', '170', '143']
['93', '178', '100', '143']
['93', '170', '48', '100']
['93', '170', '169', '100']
['93', '170', '169', '175']
['93', '170', '169', '143']
['93', '170', '100', '176']
['93', '170', '100', '175']
['93', '170', '100', '143']
['93', '170', '176', '143']
['93', '170', '175', '143']
['93', '170', '94', '143']
['93', '169', '100', '175']
['93', '169', '100', '143']
['93', '169', '176', '143']
['93', '169', '175', '143']
['93', '100', '176', '143']
['93', '100', '175', '94']
['93', '100', '175', '143']
['93', '70', '175', '143']
['93', '175', '94', '143']
['93', '175', '164', '143']
['99', '177', '170', '86']
['99', '177', '170', '175']
['99', '177', '176', '86']
['99', '177', '176', '175']
['99', '177', '86', '175']
['99', '178', '179', '176']
['99', '170', '169', '100']
['99', '170', '169', '175']
['99', '170', '86', '175']
['99', '170', '175', '143']
['99', 

['169', '70']
['169', '106']
['169', '292']
['169', '179']
['169', '176']
['169', '86']
['169', '175']
['169', '94']
['169', '143']
['1', '26']
['265', '175']
['52', '296']
['52', '51']
['52', '176']
['52', '175']
['52', '94']
['100', '70']
['100', '106']
['100', '270']
['100', '292']
['100', '147']
['100', '51']
['100', '294']
['100', '179']
['100', '176']
['100', '278']
['100', '86']
['100', '175']
['100', '94']
['100', '102']
['100', '143']
['70', '296']
['70', '179']
['70', '175']
['70', '164']
['70', '143']
['106', '292']
['106', '147']
['106', '179']
['106', '176']
['106', '175']
['106', '143']
['296', '167']
['296', '294']
['296', '179']
['296', '176']
['296', '165']
['296', '175']
['296', '164']
['296', '250']
['6', '175']
['270', '176']
['270', '269']
['270', '86']
['270', '175']
['270', '26']
['270', '143']
['292', '179']
['292', '176']
['292', '175']
['292', '143']
['107', '179']
['107', '176']
['58', '57']
['58', '176']
['58', '175']
['147', '179']
['147', '176']
['147', '1

{'170', '86', '99', '175'} -> {'177'} 0.6
X {'177', '86', '99', '175'} 4.0
{'177', '86', '99', '175'} -> {'170'} 0.75
X {'170', '177', '99', '175'} 3.0
{'170', '177', '99', '175'} -> {'86'} 1.0
X {'170', '177', '86', '99'} 3.0
{'170', '177', '86', '99'} -> {'175'} 1.0
X {'170', '177', '175'} 7.0
{'170', '177', '175'} -> {'86', '99'} 0.42857142857142855
X {'170', '177', '86'} 3.0
{'170', '177', '86'} -> {'99', '175'} 1.0
X {'170', '177', '99'} 5.0
{'170', '177', '99'} -> {'86', '175'} 0.6
parent set:  ['170', '169', '100', '175', '143'] 3.0
f_set ['7', '2']
213
72
156
8
133
108
93
76
24
132
266
35
99
61
113
19
171
60
104
273
158
263
63
128
146
59
149
177
12
268
135
160
28
9
235
32
148
42
157
75
13
41
131
23
81
27
141
272
178
170
110
48
154
50
14
55
138
105
77
97
5
30
17
297
65
3
71
46
169
1
265
52
100
36
264
78
70
106
82
296
183
6
270
292
107
58
147
38
56
51
80
167
295
29
310
57
294
49
54
45
155
73
179
34
37
176
269
202
185
182
2
10
122
288
111
309
74
307
31
40
308
64
85
79
278
86
165
1

['6', '175']
['270', '176']
['270', '269']
['270', '86']
['270', '175']
['270', '26']
['270', '143']
['292', '179']
['292', '176']
['292', '175']
['292', '143']
['107', '179']
['107', '176']
['58', '57']
['58', '176']
['58', '175']
['147', '179']
['147', '176']
['147', '175']
['147', '143']
['51', '175']
['51', '94']
['51', '143']
['167', '179']
['167', '175']
['57', '175']
['294', '179']
['294', '176']
['294', '175']
['49', '175']
['45', '176']
['45', '175']
['45', '143']
['179', '176']
['179', '278']
['179', '175']
['179', '94']
['179', '250']
['179', '143']
['34', '175']
['176', '309']
['176', '86']
['176', '175']
['176', '102']
['176', '250']
['176', '143']
['74', '175']
['64', '175']
['278', '175']
['86', '165']
['86', '175']
['86', '26']
['86', '143']
['175', '94']
['175', '164']
['175', '53']
['175', '102']
['175', '250']
['175', '26']
['175', '21']
['175', '143']
['94', '143']
['164', '143']
['102', '143']
['250', '143']
['26', '143']
f_set ['72', '108', '175']
['72', '108', '1

In [24]:
for c in confidence_full:
    print(c)

[['263', '175'], ['72'], 1.0]
[['263', '72'], ['175'], 1.0]
[['70', '138'], ['72'], 1.0]
[['72', '138'], ['70'], 1.0]
[['72', '138'], ['175'], 1.0]
[['94', '156'], ['93'], 1.0]
[['27', '99'], ['93'], 1.0]
[['27', '93'], ['99'], 1.0]
[['26', '99'], ['93'], 1.0]
[['26', '93'], ['99'], 1.0]
[['48', '143'], ['93'], 1.0]
[['71', '143'], ['93'], 1.0]
[['164', '93'], ['175'], 1.0]
[['164', '93'], ['143'], 1.0]
[['26', '143'], ['93'], 1.0]
[['26', '93'], ['143'], 1.0]
[['71', '143'], ['99'], 1.0]
[['86', '169'], ['99'], 1.0]
[['26', '143'], ['99'], 1.0]
[['26', '99'], ['143'], 1.0]
[['128', '250'], ['175'], 1.0]
[['177', '42'], ['175'], 1.0]
[['110', '176'], ['177'], 1.0]
[['58', '176'], ['177'], 1.0]
[['177', '102'], ['175'], 1.0]
[['160', '178'], ['176'], 1.0]
[['94', '178'], ['100'], 1.0]
[['170', '70'], ['175'], 1.0]
[['50', '100'], ['51'], 1.0]
[['50', '100'], ['94'], 1.0]
[['50', '143'], ['94'], 1.0]
[['70', '138'], ['175'], 1.0]
[['70', '169'], ['175'], 1.0]
[['51', '143'], ['94'], 1.0]

In [25]:
evals_full, m = get_evals(confidence_full, frequent_full, len(adj_matrix))


 [['263', '175'], ['72'], 1.0]
lift 20.038834951456312
leverage 0.0013809547953848927

 [['263', '72'], ['175'], 1.0]
lift 7.505454545454546
leverage 0.0012598307643771408

 [['70', '138'], ['72'], 1.0]
lift 20.038834951456312
leverage 0.0013809547953848927

 [['72', '138'], ['70'], 1.0]
lift 38.943396226415096
leverage 0.0014161652695150531

 [['72', '138'], ['175'], 1.0]
lift 7.505454545454546
leverage 0.0012598307643771408

 [['94', '156'], ['93'], 1.0]
lift 10.32
leverage 0.0013126464755723814

 [['27', '99'], ['93'], 1.0]
lift 10.32
leverage 0.0013126464755723814

 [['27', '93'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['26', '99'], ['93'], 1.0]
lift 10.32
leverage 0.0013126464755723814

 [['26', '93'], ['99'], 1.0]
lift 15.518796992481203
leverage 0.0013598285109067965

 [['48', '143'], ['93'], 1.0]
lift 10.32
leverage 0.0013126464755723814

 [['71', '143'], ['93'], 1.0]
lift 10.32
leverage 0.0013126464755723814

 [['164', '93'], ['175'], 1.0]
lift

In [26]:
for row in evals_full:
    print(row)

[['263', '175'], ['72'], 1.0, 20.038834951456312, 0.0013809547953848927]
[['263', '72'], ['175'], 1.0, 7.505454545454546, 0.0012598307643771408]
[['70', '138'], ['72'], 1.0, 20.038834951456312, 0.0013809547953848927]
[['72', '138'], ['70'], 1.0, 38.943396226415096, 0.0014161652695150531]
[['72', '138'], ['175'], 1.0, 7.505454545454546, 0.0012598307643771408]
[['94', '156'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['27', '99'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['27', '93'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['26', '99'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['26', '93'], ['99'], 1.0, 15.518796992481203, 0.0013598285109067965]
[['48', '143'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['71', '143'], ['93'], 1.0, 10.32, 0.0013126464755723814]
[['164', '93'], ['175'], 1.0, 7.505454545454546, 0.0012598307643771408]
[['164', '93'], ['143'], 1.0, 13.063291139240507, 0.0013422232738417163]
[['26', '143'], ['93'], 1.0, 10.32, 0.0013126464755723814]


In [27]:
for row in m:
    print(row)

[20.038834951456312, 0.0013809547953848927]
[7.505454545454546, 0.0012598307643771408]
[20.038834951456312, 0.0013809547953848927]
[38.943396226415096, 0.0014161652695150531]
[7.505454545454546, 0.0012598307643771408]
[10.32, 0.0013126464755723814]
[10.32, 0.0013126464755723814]
[15.518796992481203, 0.0013598285109067965]
[10.32, 0.0013126464755723814]
[15.518796992481203, 0.0013598285109067965]
[10.32, 0.0013126464755723814]
[10.32, 0.0013126464755723814]
[7.505454545454546, 0.0012598307643771408]
[13.063291139240507, 0.0013422232738417163]
[10.32, 0.0013126464755723814]
[13.063291139240507, 0.0013422232738417163]
[15.518796992481203, 0.0013598285109067965]
[15.518796992481203, 0.0013598285109067965]
[15.518796992481203, 0.0013598285109067965]
[13.063291139240507, 0.0013422232738417163]
[7.505454545454546, 0.0012598307643771408]
[7.505454545454546, 0.0012598307643771408]
[10.75, 0.0017577068685776095]
[10.75, 0.0017577068685776095]
[7.505454545454546, 0.0012598307643771408]
[6.5732484